### European Coffee Trip - Cafe Extractor
###### Notebook which scrapes the Website https://europeancoffeetrip.com to extract countries, cities and cafes with their addresses. The reason behind this is to create a object that can be converted into a Google Maps list allowing to show all the recommended cafes from the website on Google Maps 

In [14]:
#Dictionary structure to store the extracted data
EXAMPLE_euCoffeeTripData = {
    "exampleCountry": {
        "exampleCity": {
            "exampleCafeLink": [
            {"name": 
                "exampleCafeName"},
            {"address": 
                "ExampleStreet 1, 36043 exampleCity, exampleCountry"}
        
            ]
        }
    }
}

In [15]:
euCoffeeTripData

{'czech republic': {'https://europeancoffeetrip.com/prague/': []},
 'united kingdom': {'https://europeancoffeetrip.com/london/': []},
 'germany': {'https://europeancoffeetrip.com/berlin/': []},
 'spain': {'https://europeancoffeetrip.com/barcelona/': []},
 'france': {'https://europeancoffeetrip.com/paris/': []},
 'poland': {'https://europeancoffeetrip.com/warsaw/': []},
 'romania': {'https://europeancoffeetrip.com/bucharest/': []},
 'slovakia': {'https://europeancoffeetrip.com/bratislava/': []},
 'netherlands': {'https://europeancoffeetrip.com/amsterdam/': []},
 'hungary': {'https://europeancoffeetrip.com/budapest/': []},
 'portugal': {'https://europeancoffeetrip.com/lisbon/': []},
 'greece': {'https://europeancoffeetrip.com/athens/': []},
 'italy': {'https://europeancoffeetrip.com/rome/': []},
 'belgium': {'https://europeancoffeetrip.com/antwerp/': []},
 'ireland': {'https://europeancoffeetrip.com/dublin/': []},
 'switzerland': {'https://europeancoffeetrip.com/zurich/': []},
 'ukraine'

In [16]:
#Method to request the Website, return value is the html-file of the website
import requests

def getHMTLfile_By_Link(link:str):
    response = requests.get(link)
    if response.status_code == 200:
        print(f"Request to {link} was successful")
        return response.text
    else:
        print(f"Request to {link} failed")
        return None

###### First of all we need to extract all countries which have cities with cafes, we also extract the "first" city.
###### We can use this first city to request the city-website and extract the other cities for every country

In [17]:
country_overview = "https://europeancoffeetrip.com/city-guides/"
country_overview_HTML = getHMTLfile_By_Link(country_overview)

Request to https://europeancoffeetrip.com/city-guides/ was successful


In [18]:
from bs4 import BeautifulSoup
import re
euCoffeeTripData = {}

countryParser = BeautifulSoup(country_overview_HTML)
countries_objects = countryParser.find_all(
    "div", 
    {"data-bg": re.compile(r"https://europeancoffeetrip.com/wp-content/uploads/city-guides/countries")})

for country in countries_objects:
    extracted_country = country.find("h3", {"class": "cg-list-single-title"}).text.lower()
    try:
        #first_city = country.find("ul").find("li").find("a").text.split(" (")[0].lower()
        first_city = country.find("ul").find("li").find("a").get("href")
        if extracted_country not in euCoffeeTripData:
            euCoffeeTripData[extracted_country] = {}
        if first_city not in euCoffeeTripData[extracted_country]:
            euCoffeeTripData[extracted_country][first_city] = []
    except:
        print(f"No first city for {extracted_country}")
    
        

No first city for malta
No first city for montenegro
No first city for andorra
No first city for moldova
No first city for albania


In [ ]:
euCoffeeTripData

###### As a next step we extract all cities for one specific country. We can do so by surfing to the first-city website and extract there the other cities

In [ ]:
import time
from random import randint

for country in euCoffeeTripData:
    city_url = list(euCoffeeTripData[country].keys())[0]
    print(city_url)
        
    first_city_HTML = getHMTLfile_By_Link(city_url)
    if first_city_HTML != None:
        all_cities_Parser =  BeautifulSoup(first_city_HTML)
        all_cities = all_cities_Parser.find_all("li", {"class": "other-city"})
            
        for city in all_cities:
            extracted_other_city_url = city.find("a")["href"]
            euCoffeeTripData[country][extracted_other_city_url] = {}  
            print(f"{extracted_other_city_url=}")
            
    #to not get detected as a scanner/bruteforcer
    random_sleep = randint(5,20)
    print(f"{random_sleep}=")
    print("\n")
    time.sleep(random_sleep)

In [ ]:
euCoffeeTripData

In [26]:
#Import of the saved euCoffeeTripData - Dictionary -> just so safe requests against the Website and not create it everytime new
import ast

with open('Dictionary-Countries-Cities.txt', 'r') as file:
    dict_data = file.read()

# Convert the string representation into a Python dictionary
euCoffeeTripData = ast.literal_eval(dict_data)

print(euCoffeeTripData)
#should be ~210 cities distributed over all countries

{'czech republic': {'https://europeancoffeetrip.com/prague/': {}, 'https://europeancoffeetrip.com/brno/': {}, 'https://europeancoffeetrip.com/ostrava/': {}, 'https://europeancoffeetrip.com/olomouc/': {}, 'https://europeancoffeetrip.com/pilsen/': {}, 'https://europeancoffeetrip.com/ceskebudejovice/': {}, 'https://europeancoffeetrip.com/liberec/': {}, 'https://europeancoffeetrip.com/hradeckralove/': {}, 'https://europeancoffeetrip.com/karlovy-vary/': {}, 'https://europeancoffeetrip.com/pardubice/': {}, 'https://europeancoffeetrip.com/zlin/': {}, 'https://europeancoffeetrip.com/uherskehradiste-czechrepublic/': {}, 'https://europeancoffeetrip.com/kromeriz-czechrepublic/': {}, 'https://europeancoffeetrip.com/lednice-czechrepublic/': {}, 'https://europeancoffeetrip.com/breclav/': {}, 'https://europeancoffeetrip.com/ceskykrumlov/': {}, 'https://europeancoffeetrip.com/opava/': {}, 'https://europeancoffeetrip.com/znojmo/': {}, 'https://europeancoffeetrip.com/pisek/': {}, 'https://europeancoffee

######  Next we need to extract the links for the cafes for every city

In [27]:
test = {
    'czech republic': {
        'https://europeancoffeetrip.com/olomouc/': {},
        'https://europeancoffeetrip.com/pilsen/': {}
    }
}

In [28]:
import time
from random import randint

for country in euCoffeeTripData:
    city_urls = list(euCoffeeTripData[country].keys())
    for city_url in city_urls:
            
        cafes_HTML = getHMTLfile_By_Link(city_url)
        if cafes_HTML != None:
            cafe_Parser =  BeautifulSoup(cafes_HTML)
            cafes_link = cafe_Parser.find_all(
                        "a", 
                        {"href": re.compile(r"https://europeancoffeetrip.com/cafe/")
                    })
                
            for cafe_link in cafes_link:
                cafe_dict_link = cafe_link.get("href")
                euCoffeeTripData[country][city_url][cafe_dict_link] = []
                print(f"{cafe_dict_link=}")
                
        #to not get detected as a scanner/bruteforcer
        random_sleep = randint(5,10)
        print(f"{random_sleep}=")
        print("\n")
        time.sleep(random_sleep)
    print(f"{euCoffeeTripData=}")

https://europeancoffeetrip.com/prague/
Request to https://europeancoffeetrip.com/prague/ was successful
cafe_dict_link='https://europeancoffeetrip.com/cafe/mujsalekkavy/'
cafe_dict_link='https://europeancoffeetrip.com/cafe/elias-coffeeshop-prague/'
cafe_dict_link='https://europeancoffeetrip.com/cafe/tomcatcoffee-prague/'
cafe_dict_link='https://europeancoffeetrip.com/cafe/spellcoffee-prague/'
cafe_dict_link='https://europeancoffeetrip.com/cafe/onesipcoffee-prague/'
cafe_dict_link='https://europeancoffeetrip.com/cafe/dobroteka-prague/'
cafe_dict_link='https://europeancoffeetrip.com/cafe/mistralcafe-prague/'
cafe_dict_link='https://europeancoffeetrip.com/cafe/industracoffee-prague/'
cafe_dict_link='https://europeancoffeetrip.com/cafe/kavarna633-prague/'
cafe_dict_link='https://europeancoffeetrip.com/cafe/kavarnapodlipami-prague/'
cafe_dict_link='https://europeancoffeetrip.com/cafe/headshotcoffeefrantiskanskazahrada-prague/'
cafe_dict_link='https://europeancoffeetrip.com/cafe/helenscoffee

In [ ]:
euCoffeeTripData

###### As a last step we need to extract the cafe name and the address from the cafe link

In [7]:
#Import of the saved euCoffeeTripData - Dictionary -> just so safe requests against the Website and not create it everytime new
import ast

with open('Dict-saved4.txt', 'r', encoding='utf-8') as file:
    dict_data = file.read()

# Convert the string representation into a Python dictionary
euCoffeeTripData = ast.literal_eval(dict_data)

print(euCoffeeTripData)
#should be ~210 cities distributed over all countries

{'czech republic': {'https://europeancoffeetrip.com/prague/': {'https://europeancoffeetrip.com/cafe/mujsalekkavy/': ['Můj šálek kávy', 'Křižíkova 105, 186 00 Prague, Czech Republic'], 'https://europeancoffeetrip.com/cafe/elias-coffeeshop-prague/': ['Elias Coffee Shop', 'Štěpánská 623/40, 110 00 Prague, Czech Republic'], 'https://europeancoffeetrip.com/cafe/tomcatcoffee-prague/': ['Tomcat coffee', 'Benešova 1273/1, 152 00 Prague, Czech Republic'], 'https://europeancoffeetrip.com/cafe/spellcoffee-prague/': ['Spell Coffee', 'Jindřišská 939/20, 110 00 Prague, Czech Republic'], 'https://europeancoffeetrip.com/cafe/onesipcoffee-prague/': ['onesip coffee', 'Haštalská 755 /15, 110 00 Prague, Czech Republic'], 'https://europeancoffeetrip.com/cafe/dobroteka-prague/': ['Dobrotéka Žižkov', 'Hartigova 176, 130 00 Prague, Czech Republic'], 'https://europeancoffeetrip.com/cafe/mistralcafe-prague/': ['Mistral café', 'Valentinská 11, 110 00 Prague, Czech Republic'], 'https://europeancoffeetrip.com/cafe

In [8]:
from random import randint
import requests
from bs4 import BeautifulSoup

def rotate_proxy_request(url, proxies):
    
    user_agents = [
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/91.0.4472.124 Safari/537.36",
    "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/89.0.4389.82 Safari/537.36",
    "Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/88.0.4324.96 Safari/537.36",
    "Mozilla/5.0 (iPhone; CPU iPhone OS 14_6 like Mac OS X) AppleWebKit/605.1.15 (KHTML, like Gecko) Version/14.0 Mobile/15E148 Safari/604.1",
    "Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:90.0) Gecko/20100101 Firefox/90.0",
    "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7; rv:85.0) Gecko/20100101 Firefox/85.0"
    ]
    
    proxy = proxies[randint(0, len(proxies)-1)]
    headers = {"User-Agent": user_agents[randint(0, len(user_agents)-1)]}
    
    try:
        response = requests.get(url, proxies={"http": proxy, "https": proxy}, headers=headers, timeout=10)
        
        if response.status_code == 200:
            print(f"Request to {url} was successful with proxy {proxy}")    
            return response.text
        else:
            print(f"Request to {url} failed with proxy {proxy}")
            return None
    except:
        print(f"Probably a problem with the used proxy: {proxy}. Proxis left {len(proxies)-1}")
        proxies.remove(proxy)
        return rotate_proxy_request(url, proxies)

In [9]:
proxies = [
    "http://34.23.45.223:80",
"http://138.197.102.119:80",
"http://20.111.54.16:8123",
"http://46.47.197.210:3128",
"http://156.38.112.11:80",
"http://20.24.43.214:80",
"http://66.29.154.103:3128",
"http://20.206.106.192:8123",
"http://20.210.113.32:8123",
"http://137.66.47.158:80",
"http://116.202.121.34:3128",
"http://103.152.112.120:80",
"http://78.28.152.113:80",
"http://103.152.112.157:80",
"http://13.37.59.99:3128",
"http://13.36.104.85:80",
"http://37.27.6.46:80",
"http://44.218.183.55:80",
"http://44.195.247.145:80",
"http://103.63.26.226:1111",
"http://165.232.129.150:80",
"http://77.232.128.191:80",
"http://12.176.231.147:80",
"http://147.45.104.252:80",
"http://54.67.125.45:3128",
"http://184.169.154.119:80",
"http://13.56.192.187:80",
"http://179.41.8.151:80",
"http://193.34.144.169:80",
"http://42.113.4.233:10014",
"http://136.144.52.41:443",
"http://203.144.144.146:8080",
"http://13.208.56.180:80",
"http://3.71.239.218:3128",
"http://35.72.118.126:80",
"http://3.37.125.76:3128",
"http://35.79.120.242:3128",
"http://18.228.149.161:80",
"http://3.139.242.184:80",
"http://3.21.101.158:3128",
"http://43.201.121.81:80",
"http://54.233.119.172:3128",
"http://52.196.1.182:80",
"http://3.12.144.146:3128",
"http://116.125.141.115:80",
"http://204.236.176.61:3128",
"http://203.115.101.55:82",
"http://77.73.71.87:36482",
"http://3.212.148.199:3128",
"http://54.152.3.36:80",
"http://158.255.77.169:80",
"http://198.44.255.5:80",
"http://185.44.232.30:53281",
"http://122.160.30.99:80",
"http://129.10.76.179:80",
"http://158.255.77.168:80",
"http://54.248.238.110:80",
"http://50.169.222.243:80",
"http://50.168.72.115:80",
"http://50.168.72.116:80",
"http://47.88.59.79:82",
"http://50.169.222.241:80",
"http://219.93.101.60:80",
"http://204.236.137.68:80",
"http://203.115.101.51:82",
"http://41.59.90.171:80",
"http://66.29.154.105:3128",
"http://82.102.10.253:80",
"http://158.255.77.166:80",
"http://194.182.187.78:3128",
"http://23.247.137.142:80",
"http://176.9.239.181:80",
"http://72.10.160.174:13093",
"http://198.49.68.80:80",
"http://72.10.160.173:29439",
"http://67.43.228.253:12915",
"http://16.162.134.170:3128",
"http://85.215.64.49:80",
"http://72.10.160.93:13931",
"http://50.217.226.41:80",
"http://20.205.61.143:80",
"http://178.128.113.118:23128",
"http://162.223.90.130:80",
"http://67.43.227.226:30373",
"http://4.175.200.138:8080",
"http://172.191.74.198:8080",
"http://50.207.199.86:80",
"http://50.217.226.44:80",
"http://0.0.0.0:80",
"http://97.74.87.226:80",
"http://87.248.129.26:80",
"http://211.128.96.206:80",
"http://68.185.57.66:80",
"http://154.65.39.7:80",
"http://50.231.104.58:80",
"http://50.174.7.156:80",
"http://8.219.97.248:80",
"http://50.207.199.81:80",
"http://123.30.154.171:7777",
"http://51.89.255.67:80",
"http://127.0.0.7:80",
"http://194.87.102.94:1080",
"http://177.93.39.75:999",
"http://113.53.29.229:8080",
"http://103.147.247.124:8080",
"http://45.70.203.113:999",
"http://103.63.190.107:8080",
"http://103.118.47.243:8080",
"http://213.148.10.199:3128",
"http://203.95.199.159:8080",
"http://103.216.50.11:8080",
"http://103.38.104.166:8798",
"http://139.5.155.237:57413",
"http://202.137.134.160:8088",
"http://186.125.218.171:999",
"http://103.171.245.24:1080",
"http://114.130.153.70:58080",
"http://182.253.38.179:3128",
"http://103.180.123.19:8080",
"http://103.167.170.22:1111",
"http://190.71.24.129:999",
"http://92.60.190.79:3128",
"http://222.252.194.204:8080",
"http://67.43.228.251:3343",
"http://45.122.240.154:3128",
"http://13.38.153.36:80",
"http://13.37.89.201:80",
"http://13.38.176.104:3128",
"http://15.236.106.236:3128",
"http://160.86.242.23:8080",
"http://4.157.219.21:80",
"http://47.242.47.64:8888",
"http://3.126.147.182:80",
"http://3.127.62.252:80",
"http://3.124.133.93:3128",
"http://3.127.121.101:80",
"http://46.51.249.135:3128",
"http://43.200.77.128:3128",
"http://18.228.198.164:80",
"http://3.78.92.159:3128",
"http://52.67.10.183:80",
"http://157.254.53.50:80",
"http://101.32.14.101:1080",
"http://80.253.254.211:443",
"http://78.28.152.111:80",
"http://3.90.100.12:80",
"http://41.59.90.174:80",
"http://63.35.64.177:3128",
"http://219.65.73.81:80",
"http://44.219.175.186:80",
"http://72.10.160.90:1365",
"http://67.43.227.228:23737",
"http://72.10.160.171:10095",
"http://133.18.234.13:80",
"http://94.156.177.124:80",
"http://155.232.186.47:3128",
"http://103.175.240.49:8080",
"http://45.70.202.70:999",
"http://103.172.71.140:8080",
"http://120.28.220.26:8080",
"http://179.42.72.186:85",
"http://114.9.27.178:10001",
"http://103.160.182.103:8080",
"http://38.156.75.60:8080",
"http://170.81.77.132:2222",
"http://103.130.128.66:8080",
"http://34.87.84.105:80",
"http://40.71.46.210:8214",
"http://196.223.129.21:80",
"http://162.214.165.203:80",
"http://196.1.95.124:80",
"http://159.65.221.25:80",
"http://63.143.57.120:80",
"http://149.202.91.219:80",
"http://3.122.84.99:3128",
"http://18.185.169.150:3128",
"http://31.47.58.37:80",
"http://211.251.236.253:80",
"http://143.198.226.25:80",
"http://157.245.95.247:443",
"http://20.222.243.172:443",
"http://38.54.71.67:80",
"http://47.74.152.29:8888",
"http://103.191.92.128:80",
"http://103.122.1.14:8181",
"http://181.48.155.78:8003",
"http://103.165.157.123:8085",
"http://119.18.149.9:5020",
"http://103.133.61.230:8080",
"http://103.53.28.53:8080",
"http://154.117.154.194:8080",
"http://201.238.248.135:8118",
"http://47.91.121.127:8081",
"http://13.36.113.81:3128",
"http://23.82.137.159:80",
"http://115.72.173.60:10001",
"http://47.237.166.224:10009",
"http://191.101.80.162:80",
"http://139.162.78.109:8080",
"http://8.213.129.20:4145",
"http://103.169.255.194:6080",
"http://63.143.57.115:80",
"http://200.174.198.86:8888",
"http://63.143.57.119:80",
"http://63.143.57.116:80",
"http://84.39.112.144:3128",
"http://87.248.129.32:80",
"http://34.122.187.196:80"
]

"""euCoffeeTripData = {
    'czech republic': {
        'https://europeancoffeetrip.com/prague/': {
            'https://europeancoffeetrip.com/cafe/mujsalekkavy/': [],
            'https://europeancoffeetrip.com/cafe/elias-coffeeshop-prague/': [],
            'https://europeancoffeetrip.com/cafe/tomcatcoffee-prague/': []}},
    'united kingdom': {'https://europeancoffeetrip.com/london/': {'https://europeancoffeetrip.com/cafe/bijacoffee-london/': [],
                       }
    }}"""

"euCoffeeTripData = {\n    'czech republic': {\n        'https://europeancoffeetrip.com/prague/': {\n            'https://europeancoffeetrip.com/cafe/mujsalekkavy/': [],\n            'https://europeancoffeetrip.com/cafe/elias-coffeeshop-prague/': [],\n            'https://europeancoffeetrip.com/cafe/tomcatcoffee-prague/': []}},\n    'united kingdom': {'https://europeancoffeetrip.com/london/': {'https://europeancoffeetrip.com/cafe/bijacoffee-london/': [],\n                       }\n    }}"

In [ ]:
for country in euCoffeeTripData:
    city_urls = list(euCoffeeTripData[country].keys())
    for city_url in city_urls:
        cafe_urls = list(euCoffeeTripData[country][city_url].keys())
        for cafe_url in cafe_urls:
            if euCoffeeTripData[country][city_url][cafe_url] == []:
                address_HTML = rotate_proxy_request(cafe_url, proxies)
                if address_HTML != None:
                    address_Parser =  BeautifulSoup(address_HTML)
                    addresses_link = address_Parser.find_all(
                        "div", 
                        {"class": "cafe-name-address"})
                        
                    for address_link in addresses_link:
                        name = address_link.find("h1", {"class": "cafe-name"}).text.strip()
                        address = address_link.find("div", {"class": "cafe-address"}).text.strip()                
                        euCoffeeTripData[country][city_url][cafe_url] = [name, address]
                        print(f"{name=}\t{address=}\n")
                    
                #to not get detected as a scanner/bruteforcer
                #random_sleep = randint(5,10)
                #print(f"{random_sleep}=")
                #print("\n")
                #time.sleep(random_sleep)
            
            else:
                print(f"Eintrag für {cafe_url} exisitiert.\nName+Adresse:{euCoffeeTripData[country][city_url][cafe_url]}\n\n")
                
        print(f"{euCoffeeTripData=}")

In [11]:
import json

with open('Dict-saved5.txt', 'w', encoding='utf-8') as file:
    json.dump(euCoffeeTripData, file, ensure_ascii=False, indent=4)